# Tutorial 51: Manual Creation of Element Dataframes

This Example demonstrates the capabilities of the class Dataframes_SIR3S_Model that extends SIR3S_Model be abilities to work directley with pandas dataframes. It is shown how to create dataframes containing information about elements such as Nodes, Pipes, etc. existing in a SIR 3S Model. The methods presented are manual, user-defined and detailed. For creating more general dataframes with less input necessary, see Tutorial 52.   

# Toolkit Release

In [1]:
#pip install 

# Imports

## SIR 3S Toolkit

### Regular Import/Init

In [2]:
SIR3S_SIRGRAF_DIR = r"C:\3S\SIR 3S\SirGraf-90-15-00-22_Quebec-Upd2" #change to local path

In [3]:
from sir3stoolkit.core import wrapper

In [4]:
wrapper

<module 'sir3stoolkit.core.wrapper' from 'C:\\Users\\aUsername\\3S\\sir3stoolkit\\src\\sir3stoolkit\\core\\wrapper.py'>

In [5]:
wrapper.Initialize_Toolkit(SIR3S_SIRGRAF_DIR)

### Additional Import/Init for Dataframes class

In [6]:
from sir3stoolkit.mantle.dataframes import SIR3S_Model_Dataframes

In [7]:
s3s = SIR3S_Model_Dataframes()

Initialization complete


## Additional

In [8]:
import pandas as pd
from shapely.geometry import Point
import re
import folium
from folium.plugins import HeatMap
import numpy as np
import geopandas as gpd
from shapely import wkt
import matplotlib.pyplot as plt
import contextily as cx

# Open Model

In [9]:
s3s.OpenModel(dbName=r"Toolkit_Tutorial51_Model.db3",
              providerType=s3s.ProviderTypes.SQLite,
              Mid="M-1-0-1",
              saveCurrentlyOpenModel=False,
              namedInstance="",
              userID="",
              password="")

Model is open for further operation


# Calculate Model

In [ ]:
s3s.ExecCalculation(True) # To ensure result data

# Manual Dataframe creation

## model_data - Nodes

We can use the [generate_element_model_data_dataframe()](https://3sconsult.github.io/sir3stoolkit/references/sir3stoolkit.mantle.html#sir3stoolkit.mantle.dataframes.Dataframes_SIR3S_Model.generate_element_model_data_dataframe) method to obtain a dataframe for all instances of a specifc component type (Nodes, Pipes, etc.) with user defined model_data properties (all non-result data related to a component) to be added. For this example we will use nodes.

In this case we are interested in Nodes, let's check what model_data properties are available for this element.

In [10]:
s3s.GetPropertiesofElementType(s3s.ObjectTypes.Node)

['Name',
 'Ktyp',
 'Zkor',
 'QmEin',
 'Lfakt',
 'Fkpzon',
 'Fkfstf',
 'Fkutmp',
 'Fkfqps',
 'Fkcont',
 'Fk2lknot',
 'Beschreibung',
 'Idreferenz',
 'Iplanung',
 'Kvr',
 'Qakt',
 'Xkor',
 'Ykor',
 'NodeNamePosition',
 'ShowNodeName',
 'KvrKlartext',
 'NumberOfVERB',
 'HasBlockConnection',
 'Tk',
 'Pk',
 'InVariant',
 'GeometriesDiffer',
 'SymbolFactor',
 'bz.Drakonz',
 'bz.Fk',
 'bz.Fkpvar',
 'bz.Fkqvar',
 'bz.Fklfkt',
 'bz.PhEin',
 'bz.Tm',
 'bz.Te',
 'bz.PhMin']

In the below subcases differnt choices of parameters for creating the model_data dataframe manually are shown. Note that not all possible combination of paramters are shown here.

### Subcase 1: Minimal

Let's say for now we only want a dataframe with all node tks without any related data.

In [11]:
(s3s.generate_element_model_data_dataframe(element_type=s3s.ObjectTypes.Node
                                        ,properties=[]
                                        )).head(3)

[2026-02-12 17:24:23,091] INFO in sir3stoolkit.mantle.dataframes: [model_data] Generating model_data dataframe for element type: ObjectTypes.Node
[2026-02-12 17:24:23,096] INFO in sir3stoolkit.mantle.dataframes: [model_data] Retrieved 517 element(s) of element type ObjectTypes.Node.
[2026-02-12 17:24:23,107] INFO in sir3stoolkit.mantle.dataframes: [Resolving model_data Properties] Using 0 model_data properties.
[2026-02-12 17:24:23,109] INFO in sir3stoolkit.mantle.dataframes: [model_data] Retrieving ...
[2026-02-12 17:24:23,112] INFO in sir3stoolkit.mantle.dataframes: [model_data] Done. Shape: (517, 1)


tk
0  5669301360686511351
1  5397948523091900401
2  5239335112004772156

### Subcase 2: Specific Properties 

Let's say we now want the minimal dataframe extended with supply/return info (kvr) and height (Zkor) of the nodes.

In [12]:
(s3s.generate_element_model_data_dataframe(element_type=s3s.ObjectTypes.Node
                                        ,properties=["Kvr", "Zkor"]
                                        )).head(3)

[2026-02-12 17:24:23,130] INFO in sir3stoolkit.mantle.dataframes: [model_data] Generating model_data dataframe for element type: ObjectTypes.Node
[2026-02-12 17:24:23,132] INFO in sir3stoolkit.mantle.dataframes: [model_data] Retrieved 517 element(s) of element type ObjectTypes.Node.
[2026-02-12 17:24:23,134] INFO in sir3stoolkit.mantle.dataframes: [Resolving model_data Properties] Using 2 model_data properties.
[2026-02-12 17:24:23,135] INFO in sir3stoolkit.mantle.dataframes: [model_data] Retrieving model_data properties ['Kvr', 'Zkor']...
[2026-02-12 17:24:23,207] INFO in sir3stoolkit.mantle.dataframes: [model_data] Done. Shape: (517, 3)


tk  Kvr    Zkor
0  5669301360686511351    1  554.04
1  5397948523091900401    1  556.16
2  5239335112004772156    1  561.01

### Subcase 3: Maximal

Let's say now we want basically all available model_data (non-result data) related to nodes. 

If geometry=True, the 2D Point geometry will be added for Nodes and it will be attempted to transform the DataFrame into a GeoDataFrame using the SRID (eg. EPSG: 25832) defined in the model. If no SRID is defined, the DataFrame will remain as a DataFrame, but the geometry column with be added nonetheless.

In [13]:
(s3s.generate_element_model_data_dataframe(element_type=s3s.ObjectTypes.Node
                                        ,properties=None # Instead of an empty or filled list, we pass None to indicate we want all available properties
                                        ,geometry=True # geometry data has to be explicitly requested
                                        )).head(3)

[2026-02-12 17:24:23,221] INFO in sir3stoolkit.mantle.dataframes: [model_data] Generating model_data dataframe for element type: ObjectTypes.Node
[2026-02-12 17:24:23,224] INFO in sir3stoolkit.mantle.dataframes: [model_data] Retrieved 517 element(s) of element type ObjectTypes.Node.
[2026-02-12 17:24:23,228] INFO in sir3stoolkit.mantle.dataframes: [Resolving model_data Properties] No properties given → using ALL model_data properties for ObjectTypes.Node.
[2026-02-12 17:24:23,228] INFO in sir3stoolkit.mantle.dataframes: [Resolving model_data Properties] Using 37 model_data properties.
[2026-02-12 17:24:23,229] INFO in sir3stoolkit.mantle.dataframes: [model_data] Retrieving model_data properties ['Name', 'Ktyp', 'Zkor', 'QmEin', 'Lfakt', 'Fkpzon', 'Fkfstf', 'Fkutmp', 'Fkfqps', 'Fkcont', 'Fk2lknot', 'Beschreibung', 'Idreferenz', 'Iplanung', 'Kvr', 'Qakt', 'Xkor', 'Ykor', 'NodeNamePosition', 'ShowNodeName', 'KvrKlartext', 'NumberOfVERB', 'HasBlockConnection', 'Tk', 'Pk', 'InVariant', 'Geo

tk    Name  Ktyp    Zkor  QmEin  Lfakt  \
0  5669301360686511351  V-K03S  QKON  554.04      0      1   
1  5397948523091900401  V-K13S  QKON  556.16      0      1   
2  5239335112004772156  V-K23S  QKON  561.01      0      1   

                Fkpzon               Fkfstf               Fkutmp  Fkfqps  \
0  5520728169779652386  4798673252636751115  5591325053703727727      -1   
1  5520728169779652386  4798673252636751115  5591325053703727727      -1   
2  5520728169779652386  4798673252636751115  5591325053703727727      -1   

                Fkcont             Fk2lknot  \
0  5029128874972463118  5761544923588724980   
1  5029128874972463118  4749864932928780363   
2  5029128874972463118  4899862460906451371   

                        Beschreibung                          Idreferenz  \
0                Abzw. Am Sonnenbühl  3S3768E2953006F125B34916F6A1681667   
1  Anfangsknoten generiert von SirDB  3SC30ED954AA2F1D59B1F92FFEBCCB7B5B   
2  Anfangsknoten generiert von SirDB  3SC30ED954AA2F1D59B1F92FFEBCCB7B5B   

   Iplanung  Kvr  Qakt           Xkor          Ykor  NodeNamePosition  \
0         1    1     0  713620.267807  5.578828e+06                 1   
1         1    1     0  713602.294600  5.578860e+06                 1   
2         1    1     0  713574.061627  5.578910e+06                 1   

  ShowNodeName KvrKlartext  NumberOfVERB HasBlockConnection  \
0        False     Vorlauf             0              False   
1        False     Vorlauf             0              False   
2        False     Vorlauf             0              False   

                    Tk                   Pk InVariant GeometriesDiffer  \
0  5669301360686511351  5669301360686511351     False            False   
1  5397948523091900401  5397948523091900401     False            False   
2  5239335112004772156  5239335112004772156     False            False   

   SymbolFactor  bz.Drakonz                bz.Fk  bz.Fkpvar  bz.Fkqvar  \
0           0.2           0  5669301360686511351         -1         -1   
1           0.2           0  5397948523091900401         -1         -1   
2           0.2           0  5239335112004772156         -1         -1   

   bz.Fklfkt  bz.PhEin  bz.Tm  bz.Te  bz.PhMin                        geometry  
0         -1         0      0      0         0  POINT (713620.268 5578828.419)  
1         -1         0      0      0         0  POINT (713602.295 5578860.106)  
2         -1         0      0      0         0  POINT (713574.062 5578909.873)

### Subcase 4: Filtering + Element Type Col

Let's say we only want nodes inside a specific container and we also want to have an element type col adding "Node" to each row (useful when joining with other dataframes later).

In [14]:
for container_id in (s3s.GetTksofElementType(s3s.ObjectTypes.ObjectContainerSymbol)):
    print(f"{container_id}: {s3s.GetValue(container_id, 'Name')[0]}")

5029128874972463118: M-1-0-1
5027846505677995694: Erzeugung
5172832702839270493: TS
5152808213068069018: Laststeuerung
5467315850619588583: Sekundärwerte
5320319133990336755: Netztrennung


In [15]:
all_tks = s3s.GetTksofElementType(s3s.ObjectTypes.Node)

In [16]:
good_tks = []

In [17]:
for tk in all_tks:
    if s3s.GetValue(tk, "FkCont") == "5029128874972463118": # Main container
        if s3s.GetValue(tk, "Kvr")[0] == "1": # Supply/Vorlauf
            good_tks.append(tk)

In [18]:
(s3s.generate_element_model_data_dataframe(element_type=s3s.ObjectTypes.Node
                                        ,properties=[]
                                        ,tks=good_tks
                                        ,geometry=True
                                        ,element_type_col=True
                                        )).head(3)

[2026-02-12 17:24:24,637] INFO in sir3stoolkit.mantle.dataframes: [model_data] Generating model_data dataframe for element type: ObjectTypes.Node
[2026-02-12 17:24:24,640] INFO in sir3stoolkit.mantle.dataframes: [model_data] Retrieved 517 element(s) of element type ObjectTypes.Node.
[2026-02-12 17:24:24,642] INFO in sir3stoolkit.mantle.dataframes: [Resolving model_data Properties] Using 0 model_data properties.
[2026-02-12 17:24:24,643] INFO in sir3stoolkit.mantle.dataframes: [model_data] Retrieving geometry...
[2026-02-12 17:24:24,686] INFO in sir3stoolkit.mantle.dataframes: [model_data] Transforming DataFrame to GeoDataFrame successful with EPSG: 25832
[2026-02-12 17:24:24,686] INFO in sir3stoolkit.mantle.dataframes: [model_data] Done. Shape: (517, 3)


tk                        geometry element type
0  5669301360686511351  POINT (713620.268 5578828.419)         Node
1  5397948523091900401  POINT (713602.295 5578860.106)         Node
2  5239335112004772156  POINT (713574.062 5578909.873)         Node

## Result Data - Pipes

We can use the [generate_element_model_data_dataframe()](https://3sconsult.github.io/sir3stoolkit/references/sir3stoolkit.mantle.html#sir3stoolkit.mantle.dataframes.Dataframes_SIR3S_Model.generate_element_results_dataframe) method to obtain a dataframe for all instances of a specifc component type (Nodes, Pipes, etc.) with user defined result values for certain timestamps to be added. For this example we will use pipes.

Let's check what result properties are available for Pipes.

In [20]:
s3s.GetResultProperties_from_elementType(elementType=s3s.ObjectTypes.Pipe
                                         ,onlySelectedVectors=False 
                                         )

['A',
 'ACALC',
 'CPI',
 'CPK',
 'DH',
 'DP',
 'DRAGRED',
 'DRAKONZ',
 'DSI',
 'DSK',
 'DTTR',
 'DWVERL',
 'DWVERLABS',
 'ETAAV',
 'FS',
 'HR',
 'HVEC',
 'IAKTIV',
 'IRTRENN',
 'JV',
 'JV2',
 'LAMBDA',
 'LECKEINAUS',
 'LECKMENGE',
 'LECKORT',
 'LINEPACK',
 'LINEPACKGEOM',
 'LINEPACKRATE',
 'MAINELEMENT',
 'MAV',
 'MI',
 'MK',
 'MKOND',
 'MMAX_INST',
 'MMIN_INST',
 'MVEC',
 'MVECMAX_INST',
 'MVECMIN_INST',
 'PAV',
 'PDAMPF',
 'PHR',
 'PHVEC',
 'PMAX',
 'PMIN',
 'PR',
 'PVEC',
 'PVECMAX_INST',
 'PVECMIN_INST',
 'QI2',
 'QK2',
 'QMAV',
 'QMI',
 'QMK',
 'QMMAX_INST',
 'QMMIN_INST',
 'QMVEC',
 'QSVB',
 'RHOAV',
 'RHOI',
 'RHOK',
 'RHOVEC',
 'SVEC',
 'TAV',
 'TI',
 'TK',
 'TTRVEC',
 'TVEC',
 'TVECMAX_INST',
 'TVECMIN_INST',
 'VAV',
 'VI',
 'VK',
 'VMAX_INST',
 'VMIN_INST',
 'VOLDA',
 'WALTERI',
 'WALTERK',
 'WVL',
 'ZAUS',
 'ZEIN',
 'ZHKNR',
 'ZVEC']

Let's also check what simulation timestamps are available in the model.

In [21]:
s3s.GetTimeStamps()[0] # list of simulation timestamps

['2023-02-13 00:00:00.000 +01:00',
 '2023-02-13 01:00:00.000 +01:00',
 '2023-02-13 02:00:00.000 +01:00',
 '2023-02-13 03:00:00.000 +01:00',
 '2023-02-13 04:00:00.000 +01:00',
 '2023-02-13 05:00:00.000 +01:00',
 '2023-02-13 06:00:00.000 +01:00',
 '2023-02-13 07:00:00.000 +01:00',
 '2023-02-13 08:00:00.000 +01:00',
 '2023-02-13 09:00:00.000 +01:00',
 '2023-02-13 10:00:00.000 +01:00',
 '2023-02-13 11:00:00.000 +01:00',
 '2023-02-13 12:00:00.000 +01:00',
 '2023-02-13 13:00:00.000 +01:00',
 '2023-02-13 14:00:00.000 +01:00',
 '2023-02-13 15:00:00.000 +01:00',
 '2023-02-13 16:00:00.000 +01:00',
 '2023-02-13 17:00:00.000 +01:00',
 '2023-02-13 18:00:00.000 +01:00',
 '2023-02-13 19:00:00.000 +01:00',
 '2023-02-13 20:00:00.000 +01:00',
 '2023-02-13 21:00:00.000 +01:00',
 '2023-02-13 22:00:00.000 +01:00',
 '2023-02-13 23:00:00.000 +01:00',
 '2023-02-14 00:00:00.000 +01:00']

In [22]:
s3s.GetTimeStamps()[1] # Static

'2023-02-13 00:00:00.000 +01:00'

In the below subcases differnt choices of parameters for creating the result dataframe manually are shown. Note that not all possible combination of paramters are shown here.

### Subcase 1: Static + All Result Values

In [23]:
(s3s.generate_element_results_dataframe(element_type=s3s.ObjectTypes.Pipe
                                        ,properties=None # None => All available properties
                                        ,timestamps=[s3s.GetTimeStamps()[1]] # static
                                        )).head(3)

[2026-02-12 17:24:41,694] INFO in sir3stoolkit.mantle.dataframes: [results] Generating results dataframe for element type: ObjectTypes.Pipe
[2026-02-12 17:24:41,787] INFO in sir3stoolkit.mantle.dataframes: [Resolving Timestamps] Only static timestamp 2023-02-13 00:00:00.000 +01:00 is used
[2026-02-12 17:24:41,788] INFO in sir3stoolkit.mantle.dataframes: [Resolving Timestamps] 1 valid timestamp(s) will be used.
[2026-02-12 17:24:41,790] INFO in sir3stoolkit.mantle.dataframes: [Resolving tks] Retrieved 524 element(s) of element type ObjectTypes.Pipe.
[2026-02-12 17:24:41,793] INFO in sir3stoolkit.mantle.dataframes: [results] No properties given → using ALL result properties for ObjectTypes.Pipe.
[2026-02-12 17:24:41,794] INFO in sir3stoolkit.mantle.dataframes: [results] Using 82 result properties.
[2026-02-12 17:24:41,959] INFO in sir3stoolkit.mantle.dataframes: [results] Retrieving result values...
[2026-02-12 17:24:58,340] INFO in sir3stoolkit.mantle.dataframes: [results] Done. Shape: 

tk                                                                    5442010239090746007  \
name                                                                   Rohr V-K03S V-K13S   
end_nodes                      ('5669301360686511351', '5397948523091900401', '-1', '-1')   
property                                                                                A   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                                0.0           

tk                                                                           \
name                                                                          
end_nodes                                                                     
property                          ACALC      CPI      CPK       DH       DP   
timestamp                                                                     
2023-02-13 00:00:00.000 +01:00  99999.0  99999.0  99999.0  99999.0  99999.0   

tk                                                                            \
name                                                                           
end_nodes                                                                      
property                        DRAGRED  DRAKONZ      DSI      DSK      DTTR   
timestamp                                                                      
2023-02-13 00:00:00.000 +01:00  99999.0  99999.0  99999.0  99999.0  0.013437   

tk                                                                             \
name                                                                            
end_nodes                                                                       
property                          DWVERL DWVERLABS    ETAAV       FS       HR   
timestamp                                                                       
2023-02-13 00:00:00.000 +01:00  35.86027  1.306366  99999.0  99999.0  99999.0   

tk                                                                         \
name                                                                        
end_nodes                                                                   
property                           HVEC IAKTIV IRTRENN        JV      JV2   
timestamp                                                                   
2023-02-13 00:00:00.000 +01:00  99999.0    0.0     0.0  0.286069  99999.0   

tk                                                                     \
name                                                                    
end_nodes                                                               
property                         LAMBDA LECKEINAUS LECKMENGE  LECKORT   
timestamp                                                               
2023-02-13 00:00:00.000 +01:00  99999.0    99999.0   99999.0  99999.0   

tk                                                                             \
name                                                                            
end_nodes                                                                       
property                       LINEPACK LINEPACKGEOM LINEPACKRATE MAINELEMENT   
timestamp                                                                       
2023-02-13 00:00:00.000 +01:00  99999.0      99999.0      99999.0     99999.0   

tk                                                                            \
name                                                                           
end_nodes                                                                      
property                            MAV       MI       MK    MKOND MMAX_INST   
timestamp                                                                      
2023-02-13 00:00:00.000 +01:00  99999.0  99999.0  99999.0  99999.0   99999.0   

tk                                        \
name                                       
end_nodes                               

Note that a multi index on the columns is created, holding the most important model_data.
- Level 0: tk (device ID)
- Level 1: name (device name)
- Level 2: end_nodes (tuple of connected node IDs as string)
- Level 3: property (result name)

As can be seen a lot of 99999.0 placeholder values are inserted, because we attempt to access many result values that SIR Calc can calculate but are not requested for this model. Therefore using all available result properties(properties=None), is generally not recommended.

### Subcase 2: All Timestamps + Specific Values

In [24]:
df_pipes_2 = s3s.generate_element_results_dataframe(element_type=s3s.ObjectTypes.Pipe
                                                    ,properties=["DTTR", "PHR"] # Specify result properties of interest
                                                    ,timestamps=None # None => All available simulation timestamps
                                                    )

[2026-02-12 17:24:59,196] INFO in sir3stoolkit.mantle.dataframes: [results] Generating results dataframe for element type: ObjectTypes.Pipe
[2026-02-12 17:24:59,197] INFO in sir3stoolkit.mantle.dataframes: [Resolving Timestamps] No timestamps were given. Checking available simulation timestamps (SIR3S_Model.GetTimeStamps()[0]).
[2026-02-12 17:24:59,306] INFO in sir3stoolkit.mantle.dataframes: [Resolving Timestamps] 25 simulation timestamp(s) are available.
[2026-02-12 17:24:59,390] INFO in sir3stoolkit.mantle.dataframes: [Resolving Timestamps] 25 valid timestamp(s) will be used.
[2026-02-12 17:24:59,393] INFO in sir3stoolkit.mantle.dataframes: [Resolving tks] Retrieved 524 element(s) of element type ObjectTypes.Pipe.
[2026-02-12 17:24:59,396] INFO in sir3stoolkit.mantle.dataframes: [results] Using 2 result properties.
[2026-02-12 17:24:59,434] INFO in sir3stoolkit.mantle.dataframes: [results] Retrieving result values...
[2026-02-12 17:25:03,369] INFO in sir3stoolkit.mantle.dataframes: 

In [25]:
df_pipes_2.head(3)

tk                                                                    5442010239090746007  \
name                                                                   Rohr V-K03S V-K13S   
end_nodes                      ('5669301360686511351', '5397948523091900401', '-1', '-1')   
property                                                                             DTTR   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                           0.013437           
2023-02-13 01:00:00.000 +01:00                                           0.013437           
2023-02-13 02:00:00.000 +01:00                                           0.013437           

tk                                        \
name                                       
end_nodes                                  
property                             PHR   
timestamp                                  
2023-02-13 00:00:00.000 +01:00  0.010421   
2023-02-13 01:00:00.000 +01:00  0.010421   
2023-02-13 02:00:00.000 +01:00  0.010421   

tk                                                                    4917786378639043296  \
name                                                                   Rohr V-K13S V-K23S   
end_nodes                      ('5397948523091900401', '5239335112004772156', '-1', '-1')   
property                                                                             DTTR   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                            0.02538           
2023-02-13 01:00:00.000 +01:00                                            0.02538           
2023-02-13 02:00:00.000 +01:00                                            0.02538           

tk                                        \
name                                       
end_nodes                                  
property                             PHR   
timestamp                                  
2023-02-13 00:00:00.000 +01:00  0.014615   
2023-02-13 01:00:00.000 +01:00  0.014615   
2023-02-13 02:00:00.000 +01:00  0.014615   

tk                                                                    4762482310382009633  \
name                                                                   Rohr V-K23S V-K33S   
end_nodes                      ('5239335112004772156', '5298886695042021307', '-1', '-1')   
property                                                                             DTTR   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                           0.017832           
2023-02-13 01:00:00.000 +01:00                                           0.017832           
2023-02-13 02:00:00.000 +01:00                                           0.017832           

tk                                        \
name                                       
end_nodes                                  
property                             PHR   
timestamp                                  
2023-02-13 00:00:00.000 +01:00  0.010872   
2023-02-13 01:00:00.000 +01:00  0.010872   
2023-02-13 02:00:00.000 +01:00  0.010872   

tk                                                                    4987229536643024523  \
name                                                                   Rohr V-K33S V-K43S   
end_nodes                      ('5298886695042021307', '4993257270457791438', '-1', '-1')   
property                                                                             DTTR   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                           0.002972           
2023-02-13 01:00:00.000 +01:00                                           0.002972           
2023-02-13 02:00:00.000 +01:00                         

We can access individual values as follows.

In [26]:
df_pipes_2.loc[
    "2023-02-13 00:00:00.000 +01:00",
    ("5442010239090746007", slice(None), slice(None), "DTTR")
].item()


0.0134368

### Subcase 3: Specific Timestamps + Specific Values

We can specify the list of timestamps to include either as a list of str timestamps ...

In [27]:
(s3s.generate_element_results_dataframe(element_type=s3s.ObjectTypes.Pipe
                                        ,properties=["DTTR", "PHR"]
                                        ,timestamps=['2023-02-13 00:00:00.000 +01:00', '2023-02-13 05:00:00.000 +01:00', '2023-02-13 23:00:00.000 +01:00'] 
                                        )).head(3)

[2026-02-12 17:25:04,233] INFO in sir3stoolkit.mantle.dataframes: [results] Generating results dataframe for element type: ObjectTypes.Pipe
[2026-02-12 17:25:04,455] INFO in sir3stoolkit.mantle.dataframes: [Resolving Timestamps] 3 valid timestamp(s) will be used.
[2026-02-12 17:25:04,457] INFO in sir3stoolkit.mantle.dataframes: [Resolving tks] Retrieved 524 element(s) of element type ObjectTypes.Pipe.
[2026-02-12 17:25:04,459] INFO in sir3stoolkit.mantle.dataframes: [results] Using 2 result properties.
[2026-02-12 17:25:04,474] INFO in sir3stoolkit.mantle.dataframes: [results] Retrieving result values...
[2026-02-12 17:25:05,288] INFO in sir3stoolkit.mantle.dataframes: [results] Done. Shape: (3, 1048)


tk                                                                    5442010239090746007  \
name                                                                   Rohr V-K03S V-K13S   
end_nodes                      ('5669301360686511351', '5397948523091900401', '-1', '-1')   
property                                                                             DTTR   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                           0.013437           
2023-02-13 05:00:00.000 +01:00                                           0.013437           
2023-02-13 23:00:00.000 +01:00                                           0.013437           

tk                                        \
name                                       
end_nodes                                  
property                             PHR   
timestamp                                  
2023-02-13 00:00:00.000 +01:00  0.010421   
2023-02-13 05:00:00.000 +01:00  0.010421   
2023-02-13 23:00:00.000 +01:00  0.010421   

tk                                                                    4917786378639043296  \
name                                                                   Rohr V-K13S V-K23S   
end_nodes                      ('5397948523091900401', '5239335112004772156', '-1', '-1')   
property                                                                             DTTR   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                            0.02538           
2023-02-13 05:00:00.000 +01:00                                            0.02538           
2023-02-13 23:00:00.000 +01:00                                            0.02538           

tk                                        \
name                                       
end_nodes                                  
property                             PHR   
timestamp                                  
2023-02-13 00:00:00.000 +01:00  0.014615   
2023-02-13 05:00:00.000 +01:00  0.014615   
2023-02-13 23:00:00.000 +01:00  0.014615   

tk                                                                    4762482310382009633  \
name                                                                   Rohr V-K23S V-K33S   
end_nodes                      ('5239335112004772156', '5298886695042021307', '-1', '-1')   
property                                                                             DTTR   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                           0.017832           
2023-02-13 05:00:00.000 +01:00                                           0.017832           
2023-02-13 23:00:00.000 +01:00                                           0.017832           

tk                                        \
name                                       
end_nodes                                  
property                             PHR   
timestamp                                  
2023-02-13 00:00:00.000 +01:00  0.010872   
2023-02-13 05:00:00.000 +01:00  0.010872   
2023-02-13 23:00:00.000 +01:00  0.010872   

tk                                                                    4987229536643024523  \
name                                                                   Rohr V-K33S V-K43S   
end_nodes                      ('5298886695042021307', '4993257270457791438', '-1', '-1')   
property                                                                             DTTR   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                           0.002972           
2023-02-13 05:00:00.000 +01:00                                           0.002972           
2023-02-13 23:00:00.000 +01:00                         

... or as a list of int indices.

In [28]:
simulation_timestamps=s3s.GetTimeStamps()[0]

In [29]:
for idx, timestamp in enumerate(simulation_timestamps):
    print(idx, timestamp)

0 2023-02-13 00:00:00.000 +01:00
1 2023-02-13 01:00:00.000 +01:00
2 2023-02-13 02:00:00.000 +01:00
3 2023-02-13 03:00:00.000 +01:00
4 2023-02-13 04:00:00.000 +01:00
5 2023-02-13 05:00:00.000 +01:00
6 2023-02-13 06:00:00.000 +01:00
7 2023-02-13 07:00:00.000 +01:00
8 2023-02-13 08:00:00.000 +01:00
9 2023-02-13 09:00:00.000 +01:00
10 2023-02-13 10:00:00.000 +01:00
11 2023-02-13 11:00:00.000 +01:00
12 2023-02-13 12:00:00.000 +01:00
13 2023-02-13 13:00:00.000 +01:00
14 2023-02-13 14:00:00.000 +01:00
15 2023-02-13 15:00:00.000 +01:00
16 2023-02-13 16:00:00.000 +01:00
17 2023-02-13 17:00:00.000 +01:00
18 2023-02-13 18:00:00.000 +01:00
19 2023-02-13 19:00:00.000 +01:00
20 2023-02-13 20:00:00.000 +01:00
21 2023-02-13 21:00:00.000 +01:00
22 2023-02-13 22:00:00.000 +01:00
23 2023-02-13 23:00:00.000 +01:00
24 2023-02-14 00:00:00.000 +01:00


In [30]:
(s3s.generate_element_results_dataframe(element_type=s3s.ObjectTypes.Pipe
                                        ,properties=["DTTR", "PHR"]
                                        ,timestamps=[0, 5, -2] 
                                        )).head(3)

[2026-02-12 17:25:06,185] INFO in sir3stoolkit.mantle.dataframes: [results] Generating results dataframe for element type: ObjectTypes.Pipe
[2026-02-12 17:25:06,267] INFO in sir3stoolkit.mantle.dataframes: [Resolving Timestamps] 3 valid timestamp(s) will be used.
[2026-02-12 17:25:06,269] INFO in sir3stoolkit.mantle.dataframes: [Resolving tks] Retrieved 524 element(s) of element type ObjectTypes.Pipe.
[2026-02-12 17:25:06,271] INFO in sir3stoolkit.mantle.dataframes: [results] Using 2 result properties.
[2026-02-12 17:25:06,298] INFO in sir3stoolkit.mantle.dataframes: [results] Retrieving result values...
[2026-02-12 17:25:06,859] INFO in sir3stoolkit.mantle.dataframes: [results] Done. Shape: (3, 1048)


tk                                                                    5442010239090746007  \
name                                                                   Rohr V-K03S V-K13S   
end_nodes                      ('5669301360686511351', '5397948523091900401', '-1', '-1')   
property                                                                             DTTR   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                           0.013437           
2023-02-13 05:00:00.000 +01:00                                           0.013437           
2023-02-13 23:00:00.000 +01:00                                           0.013437           

tk                                        \
name                                       
end_nodes                                  
property                             PHR   
timestamp                                  
2023-02-13 00:00:00.000 +01:00  0.010421   
2023-02-13 05:00:00.000 +01:00  0.010421   
2023-02-13 23:00:00.000 +01:00  0.010421   

tk                                                                    4917786378639043296  \
name                                                                   Rohr V-K13S V-K23S   
end_nodes                      ('5397948523091900401', '5239335112004772156', '-1', '-1')   
property                                                                             DTTR   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                            0.02538           
2023-02-13 05:00:00.000 +01:00                                            0.02538           
2023-02-13 23:00:00.000 +01:00                                            0.02538           

tk                                        \
name                                       
end_nodes                                  
property                             PHR   
timestamp                                  
2023-02-13 00:00:00.000 +01:00  0.014615   
2023-02-13 05:00:00.000 +01:00  0.014615   
2023-02-13 23:00:00.000 +01:00  0.014615   

tk                                                                    4762482310382009633  \
name                                                                   Rohr V-K23S V-K33S   
end_nodes                      ('5239335112004772156', '5298886695042021307', '-1', '-1')   
property                                                                             DTTR   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                           0.017832           
2023-02-13 05:00:00.000 +01:00                                           0.017832           
2023-02-13 23:00:00.000 +01:00                                           0.017832           

tk                                        \
name                                       
end_nodes                                  
property                             PHR   
timestamp                                  
2023-02-13 00:00:00.000 +01:00  0.010872   
2023-02-13 05:00:00.000 +01:00  0.010872   
2023-02-13 23:00:00.000 +01:00  0.010872   

tk                                                                    4987229536643024523  \
name                                                                   Rohr V-K33S V-K43S   
end_nodes                      ('5298886695042021307', '4993257270457791438', '-1', '-1')   
property                                                                             DTTR   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                           0.002972           
2023-02-13 05:00:00.000 +01:00                                           0.002972           
2023-02-13 23:00:00.000 +01:00                         

### Subcase 4: Specific Timestamps + Specific Values + Filtering

If we want to filter for more than just the container, we have to filter tks outside the function and then pass them. Works same way as for model_data.

In [31]:
all_tks = s3s.GetTksofElementType(s3s.ObjectTypes.Pipe)

In [32]:
len(all_tks)

524

In [33]:
good_tks = []

In [34]:
for tk in all_tks:
    if s3s.GetValue(tk, "FkCont")[0] == "5029128874972463118":
        if s3s.GetValue(tk, "bz.Irtrenn")[0] == "0": # Rohr nicht getrennt
            good_tks.append(tk)

In [35]:
len(good_tks)

480

In [36]:
(s3s.generate_element_results_dataframe(element_type=s3s.ObjectTypes.Pipe
                                        ,tks=good_tks # here we specify that not all available tks should be used
                                        ,properties=["DTTR", "PHR"]
                                        ,timestamps=[0, 5, -2] 
                                        )).head(3)

[2026-02-12 17:25:08,110] INFO in sir3stoolkit.mantle.dataframes: [results] Generating results dataframe for element type: ObjectTypes.Pipe
[2026-02-12 17:25:08,272] INFO in sir3stoolkit.mantle.dataframes: [Resolving Timestamps] 3 valid timestamp(s) will be used.
[2026-02-12 17:25:08,276] INFO in sir3stoolkit.mantle.dataframes: [Resolving tks] Retrieved 524 element(s) of element type ObjectTypes.Pipe.
[2026-02-12 17:25:08,283] INFO in sir3stoolkit.mantle.dataframes: [Resolving tks] 480 tks remain after filtering for given tks.
[2026-02-12 17:25:08,287] INFO in sir3stoolkit.mantle.dataframes: [results] Using 2 result properties.
[2026-02-12 17:25:08,312] INFO in sir3stoolkit.mantle.dataframes: [results] Retrieving result values...
[2026-02-12 17:25:09,459] INFO in sir3stoolkit.mantle.dataframes: [results] Done. Shape: (3, 960)


tk                                                                    5442010239090746007  \
name                                                                   Rohr V-K03S V-K13S   
end_nodes                      ('5669301360686511351', '5397948523091900401', '-1', '-1')   
property                                                                             DTTR   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                           0.013437           
2023-02-13 05:00:00.000 +01:00                                           0.013437           
2023-02-13 23:00:00.000 +01:00                                           0.013437           

tk                                        \
name                                       
end_nodes                                  
property                             PHR   
timestamp                                  
2023-02-13 00:00:00.000 +01:00  0.010421   
2023-02-13 05:00:00.000 +01:00  0.010421   
2023-02-13 23:00:00.000 +01:00  0.010421   

tk                                                                    4917786378639043296  \
name                                                                   Rohr V-K13S V-K23S   
end_nodes                      ('5397948523091900401', '5239335112004772156', '-1', '-1')   
property                                                                             DTTR   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                            0.02538           
2023-02-13 05:00:00.000 +01:00                                            0.02538           
2023-02-13 23:00:00.000 +01:00                                            0.02538           

tk                                        \
name                                       
end_nodes                                  
property                             PHR   
timestamp                                  
2023-02-13 00:00:00.000 +01:00  0.014615   
2023-02-13 05:00:00.000 +01:00  0.014615   
2023-02-13 23:00:00.000 +01:00  0.014615   

tk                                                                    4762482310382009633  \
name                                                                   Rohr V-K23S V-K33S   
end_nodes                      ('5239335112004772156', '5298886695042021307', '-1', '-1')   
property                                                                             DTTR   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                           0.017832           
2023-02-13 05:00:00.000 +01:00                                           0.017832           
2023-02-13 23:00:00.000 +01:00                                           0.017832           

tk                                        \
name                                       
end_nodes                                  
property                             PHR   
timestamp                                  
2023-02-13 00:00:00.000 +01:00  0.010872   
2023-02-13 05:00:00.000 +01:00  0.010872   
2023-02-13 23:00:00.000 +01:00  0.010872   

tk                                                                    4987229536643024523  \
name                                                                   Rohr V-K33S V-K43S   
end_nodes                      ('5298886695042021307', '4993257270457791438', '-1', '-1')   
property                                                                             DTTR   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                           0.002972           
2023-02-13 05:00:00.000 +01:00                                           0.002972           
2023-02-13 23:00:00.000 +01:00                         

### Subcase 5: Specific Vectorized results + Specific Timestamps

For pipes we have interior point result values. These are usually found as vectors with the postfix VEC.

In [37]:
available_result_props=s3s.GetResultProperties_from_elementType(s3s.ObjectTypes.Pipe,False)

In [38]:
available_result_props

['A',
 'ACALC',
 'CPI',
 'CPK',
 'DH',
 'DP',
 'DRAGRED',
 'DRAKONZ',
 'DSI',
 'DSK',
 'DTTR',
 'DWVERL',
 'DWVERLABS',
 'ETAAV',
 'FS',
 'HR',
 'HVEC',
 'IAKTIV',
 'IRTRENN',
 'JV',
 'JV2',
 'LAMBDA',
 'LECKEINAUS',
 'LECKMENGE',
 'LECKORT',
 'LINEPACK',
 'LINEPACKGEOM',
 'LINEPACKRATE',
 'MAINELEMENT',
 'MAV',
 'MI',
 'MK',
 'MKOND',
 'MMAX_INST',
 'MMIN_INST',
 'MVEC',
 'MVECMAX_INST',
 'MVECMIN_INST',
 'PAV',
 'PDAMPF',
 'PHR',
 'PHVEC',
 'PMAX',
 'PMIN',
 'PR',
 'PVEC',
 'PVECMAX_INST',
 'PVECMIN_INST',
 'QI2',
 'QK2',
 'QMAV',
 'QMI',
 'QMK',
 'QMMAX_INST',
 'QMMIN_INST',
 'QMVEC',
 'QSVB',
 'RHOAV',
 'RHOI',
 'RHOK',
 'RHOVEC',
 'SVEC',
 'TAV',
 'TI',
 'TK',
 'TTRVEC',
 'TVEC',
 'TVECMAX_INST',
 'TVECMIN_INST',
 'VAV',
 'VI',
 'VK',
 'VMAX_INST',
 'VMIN_INST',
 'VOLDA',
 'WALTERI',
 'WALTERK',
 'WVL',
 'ZAUS',
 'ZEIN',
 'ZHKNR',
 'ZVEC']

In [39]:
available_result_vector_props=[available_result_props for available_result_props in available_result_props if "VEC" in available_result_props]

In [40]:
available_result_vector_props

['HVEC',
 'MVEC',
 'MVECMAX_INST',
 'MVECMIN_INST',
 'PHVEC',
 'PVEC',
 'PVECMAX_INST',
 'PVECMIN_INST',
 'QMVEC',
 'RHOVEC',
 'SVEC',
 'TTRVEC',
 'TVEC',
 'TVECMAX_INST',
 'TVECMIN_INST',
 'ZVEC']

In [41]:
df_pipes = s3s.generate_element_results_dataframe(element_type=s3s.ObjectTypes.Pipe
                                        ,properties=["TTRVEC", "MVEC", "DTTR"]
                                        ,timestamps=[0, 5, -2] 
                                        )

[2026-02-12 17:25:10,421] INFO in sir3stoolkit.mantle.dataframes: [results] Generating results dataframe for element type: ObjectTypes.Pipe
[2026-02-12 17:25:10,510] INFO in sir3stoolkit.mantle.dataframes: [Resolving Timestamps] 3 valid timestamp(s) will be used.
[2026-02-12 17:25:10,510] INFO in sir3stoolkit.mantle.dataframes: [Resolving tks] Retrieved 524 element(s) of element type ObjectTypes.Pipe.
[2026-02-12 17:25:10,517] INFO in sir3stoolkit.mantle.dataframes: [results] Using 3 result properties.
[2026-02-12 17:25:10,541] INFO in sir3stoolkit.mantle.dataframes: [results] Retrieving result values...
[2026-02-12 17:25:11,504] INFO in sir3stoolkit.mantle.dataframes: [results] Done. Shape: (3, 1572)


In [42]:
df_pipes.head(3)

tk                                                                    5442010239090746007  \
name                                                                   Rohr V-K03S V-K13S   
end_nodes                      ('5669301360686511351', '5397948523091900401', '-1', '-1')   
property                                                                           TTRVEC   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00  0.3226847\t0.3260439\t0.3294031\t0.3327623\t0....           
2023-02-13 05:00:00.000 +01:00  0.3226847\t0.3260439\t0.3294031\t0.3327623\t0....           
2023-02-13 23:00:00.000 +01:00  0.3226847\t0.3260439\t0.3294031\t0.3327623\t0....           

tk                                                                                \
name                                                                               
end_nodes                                                                          
property                                                                    MVEC   
timestamp                                                                          
2023-02-13 00:00:00.000 +01:00  14.68005\t14.68005\t14.68005\t14.68005\t14.68005   
2023-02-13 05:00:00.000 +01:00  14.68005\t14.68005\t14.68005\t14.68005\t14.68005   
2023-02-13 23:00:00.000 +01:00  14.68005\t14.68005\t14.68005\t14.68005\t14.68005   

tk                                        \
name                                       
end_nodes                                  
property                            DTTR   
timestamp                                  
2023-02-13 00:00:00.000 +01:00  0.013437   
2023-02-13 05:00:00.000 +01:00  0.013437   
2023-02-13 23:00:00.000 +01:00  0.013437   

tk                                                                    4917786378639043296  \
name                                                                   Rohr V-K13S V-K23S   
end_nodes                      ('5397948523091900401', '5239335112004772156', '-1', '-1')   
property                                                                           TTRVEC   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00  0.3361215\t0.3403515\t0.3445815\t0.3488115\t0....           
2023-02-13 05:00:00.000 +01:00  0.3361215\t0.3403515\t0.3445815\t0.3488115\t0....           
2023-02-13 23:00:00.000 +01:00  0.3361215\t0.3403515\t0.3445815\t0.3488115\t0....           

tk                                                                                 \
name                                                                                
end_nodes                                                                           
property                                                                     MVEC   
timestamp                                                                           
2023-02-13 00:00:00.000 +01:00  8.239944\t8.239944\t8.239944\t8.239944\t8.2399...   
2023-02-13 05:00:00.000 +01:00  8.239944\t8.239944\t8.239944\t8.239944\t8.2399...   
2023-02-13 23:00:00.000 +01:00  8.239944\t8.239944\t8.239944\t8.239944\t8.2399...   

tk                                       \
name                                      
end_nodes                                 
property                           DTTR   
timestamp                                 
2023-02-13 00:00:00.000 +01:00  0.02538   
2023-02-13 05:00:00.000 +01:00  0.02538   
2023-02-13 23:00:00.000 +01:00  0.02538   

tk                                                                    4762482310382009633  \
name                                                                   Rohr V-K23S V-K33S   
end_nodes                      ('5239335112004772156', '5298886695042021307', '-1', '-1')   
property                                                                           TTRVEC   
timestamp                                                                             

As can be seen, the vectorized result values are written as strings with "/" seperators. For better access we can extend these values to a multiindex using [add_interior_points_as_multiindex()](https://3sconsult.github.io/sir3stoolkit/references/sir3stoolkit.mantle.html#sir3stoolkit.mantle.dataframes.SIR3S_Model_Dataframes.add_interior_points_as_multiindex).

In [43]:
df_pipes_interior_points = s3s.add_interior_points_as_multiindex(df_pipes)

In [44]:
df_pipes_interior_points.head(3)

tk                                                                    5442010239090746007  \
name                                                                   Rohr V-K03S V-K13S   
end_nodes                      ('5669301360686511351', '5397948523091900401', '-1', '-1')   
property                                                                           TTRVEC   
interior points                                                                        0    
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                           0.322685           
2023-02-13 05:00:00.000 +01:00                                           0.322685           
2023-02-13 23:00:00.000 +01:00                                           0.322685           

tk                                                                      \
name                                                                     
end_nodes                                                                
property                                                                 
interior points                       1         2         3         4    
timestamp                                                                
2023-02-13 00:00:00.000 +01:00  0.326044  0.329403  0.332762  0.336122   
2023-02-13 05:00:00.000 +01:00  0.326044  0.329403  0.332762  0.336122   
2023-02-13 23:00:00.000 +01:00  0.326044  0.329403  0.332762  0.336122   

tk                                                                      \
name                                                                     
end_nodes                                                                
property                            MVEC                                 
interior points                       0         1         2         3    
timestamp                                                                
2023-02-13 00:00:00.000 +01:00  14.68005  14.68005  14.68005  14.68005   
2023-02-13 05:00:00.000 +01:00  14.68005  14.68005  14.68005  14.68005   
2023-02-13 23:00:00.000 +01:00  14.68005  14.68005  14.68005  14.68005   

tk                                                  \
name                                                 
end_nodes                                            
property                                      DTTR   
interior points                       4        -1    
timestamp                                            
2023-02-13 00:00:00.000 +01:00  14.68005  0.013437   
2023-02-13 05:00:00.000 +01:00  14.68005  0.013437   
2023-02-13 23:00:00.000 +01:00  14.68005  0.013437   

tk                                                                    4917786378639043296  \
name                                                                   Rohr V-K13S V-K23S   
end_nodes                      ('5397948523091900401', '5239335112004772156', '-1', '-1')   
property                                                                           TTRVEC   
interior points                                                                        0    
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                           0.336122           
2023-02-13 05:00:00.000 +01:00                                           0.336122           
2023-02-13 23:00:00.000 +01:00                                           0.336122           

tk                                                                      \
name                                                                     
end_nodes                                                                
property                                                                 
interior points                       1         2         3         4    
timestamp                                                                
2023-02-13 00:00:00.000 +01:00  0.340351  0.344581  0.34881

Note that an additional multiindex is created that indexes the interior points. Non-vectorized properties get index -1 in the new multiindex .

We can access individual values as follows.

In [45]:
df_pipes_interior_points.loc[
    "2023-02-13 00:00:00.000 +01:00",
    ("5442010239090746007", slice(None), slice(None), "MVEC", 2)
].item()


14.68005

## Merge model_data and Result Dataframes (for one timestamp)

### Create Dataframes - For pipes

#### model_data

In [46]:
df_pipes_model_data = s3s.generate_element_model_data_dataframe(element_type=s3s.ObjectTypes.Pipe
                                                            ,properties=["L", "DN"]
                                                            ,geometry=True
                                                            )

[2026-02-12 17:25:19,112] INFO in sir3stoolkit.mantle.dataframes: [model_data] Generating model_data dataframe for element type: ObjectTypes.Pipe
[2026-02-12 17:25:19,114] INFO in sir3stoolkit.mantle.dataframes: [model_data] Retrieved 524 element(s) of element type ObjectTypes.Pipe.
[2026-02-12 17:25:19,116] INFO in sir3stoolkit.mantle.dataframes: [Resolving model_data Properties] Using 2 model_data properties.
[2026-02-12 17:25:19,118] INFO in sir3stoolkit.mantle.dataframes: [model_data] Retrieving model_data properties ['L', 'DN'], geometry...
[2026-02-12 17:25:19,242] INFO in sir3stoolkit.mantle.dataframes: [model_data] Transforming DataFrame to GeoDataFrame successful with EPSG: 25832
[2026-02-12 17:25:19,242] INFO in sir3stoolkit.mantle.dataframes: [model_data] Done. Shape: (524, 4)


In [47]:
df_pipes_model_data.head(3)

tk         L   DN  \
0  5442010239090746007  36.42935  150   
1  4917786378639043296  57.21781  125   
2  4762482310382009633  40.99482  125   

                                            geometry  
0  LINESTRING (713620.268 5578828.419, 713602.295...  
1  LINESTRING (713602.295 5578860.106, 713574.062...  
2  LINESTRING (713574.062 5578909.873, 713553.84 ...

#### Results

In [48]:
df_pipes_results = s3s.generate_element_results_dataframe(element_type=s3s.ObjectTypes.Pipe
                                                        ,properties=["DTTR", "PHR", "PVEC"]
                                                        ,timestamps=[0] 
                                                        )

[2026-02-12 17:25:19,272] INFO in sir3stoolkit.mantle.dataframes: [results] Generating results dataframe for element type: ObjectTypes.Pipe
[2026-02-12 17:25:19,338] INFO in sir3stoolkit.mantle.dataframes: [Resolving Timestamps] Only static timestamp 2023-02-13 00:00:00.000 +01:00 is used
[2026-02-12 17:25:19,338] INFO in sir3stoolkit.mantle.dataframes: [Resolving Timestamps] 1 valid timestamp(s) will be used.
[2026-02-12 17:25:19,342] INFO in sir3stoolkit.mantle.dataframes: [Resolving tks] Retrieved 524 element(s) of element type ObjectTypes.Pipe.
[2026-02-12 17:25:19,345] INFO in sir3stoolkit.mantle.dataframes: [results] Using 3 result properties.
[2026-02-12 17:25:19,361] INFO in sir3stoolkit.mantle.dataframes: [results] Retrieving result values...
[2026-02-12 17:25:19,743] INFO in sir3stoolkit.mantle.dataframes: [results] Done. Shape: (1, 1572)


In [49]:
df_pipes_results.head(3)

tk                                                                    5442010239090746007  \
name                                                                   Rohr V-K03S V-K13S   
end_nodes                      ('5669301360686511351', '5397948523091900401', '-1', '-1')   
property                                                                             DTTR   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                           0.013437           

tk                                        \
name                                       
end_nodes                                  
property                             PHR   
timestamp                                  
2023-02-13 00:00:00.000 +01:00  0.010421   

tk                                                                              \
name                                                                             
end_nodes                                                                        
property                                                                  PVEC   
timestamp                                                                        
2023-02-13 00:00:00.000 +01:00  4.502625\t4.44982\t4.397015\t4.34421\t4.291405   

tk                                                                    4917786378639043296  \
name                                                                   Rohr V-K13S V-K23S   
end_nodes                      ('5397948523091900401', '5239335112004772156', '-1', '-1')   
property                                                                             DTTR   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                            0.02538           

tk                                        \
name                                       
end_nodes                                  
property                             PHR   
timestamp                                  
2023-02-13 00:00:00.000 +01:00  0.014615   

tk                                                                                 \
name                                                                                
end_nodes                                                                           
property                                                                     PVEC   
timestamp                                                                           
2023-02-13 00:00:00.000 +01:00  4.291405\t4.2124\t4.1334\t4.054395\t3.975395\t...   

tk                                                                    4762482310382009633  \
name                                                                   Rohr V-K23S V-K33S   
end_nodes                      ('5239335112004772156', '5298886695042021307', '-1', '-1')   
property                                                                             DTTR   
timestamp                                                                                   
2023-02-13 00:00:00.000 +01:00                                           0.017832           

tk                                        \
name                                       
end_nodes                                  
property                             PHR   
timestamp                                  
2023-02-13 00:00:00.000 +01:00  0.010872   

tk                                                                                 \
name                                                                                
end_nodes                                                                           
property                                                                     PVEC   
timestamp                                                                           
2023-02-13 00:00:00.000 +01:00  3.81739\t3.77638\t3.735365\t3.69435\t3.653335\...   

tk           

### Merge

In [50]:
df_pipes_results.columns = df_pipes_results.columns.droplevel([1, 2])
df_pipes_results = df_pipes_results.T.unstack(level=0).T
df_pipes_results = df_pipes_results.droplevel(0, axis=0)
df_pipes = df_pipes_model_data.merge(on="tk",
                    how="outer",
                    right=df_pipes_results)

In [51]:
df_pipes.head(3)

tk          L   DN  \
0  4614463970292122863   7.780674  999   
1  4615723899944629797  64.287240  999   
2  4621030304810285220   3.956838  100   

                                            geometry      DTTR       PHR  \
0  LINESTRING (714262.483 5578857.42, 714269.543 ...  7.780674       0.0   
1  LINESTRING (713738.297 5579219.902, 713793.23 ...  64.28724       0.0   
2  LINESTRING (713650.613 5578990.488, 713649.498...  0.002291  0.000835   

                                                PVEC  
0                                  1.615055\t1.68863  
1  3.304715\t3.3455\t3.38628\t3.42706\t3.46784\t3...  
2                                  2.210375\t2.19867

## Expand vectorized results

### multiindex

In [52]:
df_vector_multiindex = s3s.add_interior_points_as_multiindex(df_pipes)

In [53]:
df_vector_multiindex.head(3)

tk          L   DN  \
interior points                  -1         -1   -1    
0                4614463970292122863   7.780674  999   
1                4615723899944629797  64.287240  999   
2                4621030304810285220   3.956838  100   

                                                          geometry      DTTR  \
interior points                                                -1        -1    
0                LINESTRING (714262.483 5578857.42, 714269.543 ...  7.780674   
1                LINESTRING (713738.297 5579219.902, 713793.23 ...  64.28724   
2                LINESTRING (713650.613 5578990.488, 713649.498...  0.002291   

                      PHR      PVEC                                      \
interior points       -1         0        1        2        3        4    
0                     0.0  1.615055  1.68863      NaN      NaN      NaN   
1                     0.0  3.304715  3.34550  3.38628  3.42706  3.46784   
2                0.000835  2.210375  2.19867      NaN      NaN      NaN   

                                                                               \
interior points       5       6        7   8   9   10  11  12  13  14  15  16   
0                    NaN     NaN      NaN NaN NaN NaN NaN NaN NaN NaN NaN NaN   
1                3.50862  3.5494  3.59018 NaN NaN NaN NaN NaN NaN NaN NaN NaN   
2                    NaN     NaN      NaN NaN NaN NaN NaN NaN NaN NaN NaN NaN   

                     
interior points  17  
0               NaN  
1               NaN  
2               NaN

### flat cols

In [54]:
df_vector_flat = s3s.add_interior_points_as_flat_cols(df_pipes)

In [55]:
df_vector_flat.head(3)

tk          L   DN  \
0  4614463970292122863   7.780674  999   
1  4615723899944629797  64.287240  999   
2  4621030304810285220   3.956838  100   

                                            geometry      DTTR       PHR  \
0  LINESTRING (714262.483 5578857.42, 714269.543 ...  7.780674       0.0   
1  LINESTRING (713738.297 5579219.902, 713793.23 ...  64.28724       0.0   
2  LINESTRING (713650.613 5578990.488, 713649.498...  0.002291  0.000835   

     PVEC_0   PVEC_1   PVEC_2   PVEC_3   PVEC_4   PVEC_5  PVEC_6   PVEC_7  \
0  1.615055  1.68863      NaN      NaN      NaN      NaN     NaN      NaN   
1  3.304715  3.34550  3.38628  3.42706  3.46784  3.50862  3.5494  3.59018   
2  2.210375  2.19867      NaN      NaN      NaN      NaN     NaN      NaN   

   PVEC_8  PVEC_9  PVEC_10  PVEC_11  PVEC_12  PVEC_13  PVEC_14  PVEC_15  \
0     NaN     NaN      NaN      NaN      NaN      NaN      NaN      NaN   
1     NaN     NaN      NaN      NaN      NaN      NaN      NaN      NaN   
2     NaN     NaN      NaN      NaN      NaN      NaN      NaN      NaN   

   PVEC_16  PVEC_17  
0      NaN      NaN  
1      NaN      NaN  
2      NaN      NaN